# Preliminaries

First, make sure the virtual environment is activated inside of the Jupyter notebook so we have access to all the necessary packages. That is, make sure to add the virtual environment to the available kernels for the notebook.

Also, make sure this notebook is in the proper directory inside the larger project directory. This is important for some relative imports and file paths later.

In [1]:
# See available packages
!pip list

Package                            Version
---------------------------------- ---------------
alabaster                          0.7.12
altair                             4.1.0
altgraph                           0.17.3
anaconda-client                    1.11.0
anaconda-navigator                 2.3.2
anaconda-project                   0.11.1
antlr4-python3-runtime             4.9.3
anyio                              3.5.0
appdirs                            1.4.4
applaunchservices                  0.2.1
appnope                            0.1.2
appscript                          1.1.2
argh                               0.26.2
argon2-cffi                        21.3.0
argon2-cffi-bindings               21.2.0
asn1crypto                         1.5.1
astor                              0.8.1
astroid                            2.11.7
astropy                            5.1
asttokens                          2.0.5
atomicwrites                       1.4.0
attrs                              22.1

In [2]:
# Some additional installations/updates for some packages
!pip install --upgrade pip --quiet
!pip install --upgrade ctgan --quiet
!pip install sdv opacus autodp smartnoise-synth --quiet

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
sdv 0.17.2 requires ctgan<0.6,>=0.5.2, but you have ctgan 0.7.4 which is incompatible.
sdv 0.17.2 requires rdt<1.3.0,>=1.2.0, but you have rdt 1.6.1 which is incompatible.


In [3]:
# Import packages and modules
import numpy as np
import pandas as pd
import time
import json
import itertools
from sklearn.ensemble import IsolationForest

# Import specific modules from tapas
import tapas.datasets
import tapas.generators
import tapas.attacks
import tapas.threat_models
import tapas.report

from tapas.generators import Generator, ReprosynGenerator, Raw

# Some fancy displays when training/testing.
import tqdm

# For defining attacks
from sklearn.ensemble import RandomForestClassifier

# Import modules from AIM
from mbi import Dataset, Domain

# Generators
from modules.myctgan import CTGAN
from modules.myctgan import DPCTGAN
from modules.myctgan import PATEGAN

/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/mbi/__init__.py:15: UserWarning: MixtureInference disabled, please install jax and jaxlib
  warnings.warn('MixtureInference disabled, please install jax and jaxlib')
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Load Data

In [4]:
# Read in csv data file
df = pd.read_csv("../data/texas-big.csv", index_col=None)[:1000]    # Texas1000 dataset
cols = df.columns
dtype_dict = {"DISCHARGE": "str", **{col: 'str' for col in cols[1:12]}, **{col: 'float64' for col in cols[12:]}}
df = df.astype(dtype_dict)

/var/folders/k1/bz3mf5t15h96yvggnqmy2bj40000gn/T/ipykernel_10704/2590285146.py:2: DtypeWarning: Columns (1,5) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("../data/texas-big.csv", index_col=None)[:1000]    # Texas1000 dataset


In [5]:
# Create TabularDataset object
data = tapas.datasets.TabularDataset(data=df, 
                                     description=tapas.datasets.DataDescription(json.load(open("../data/texas-big.json"))))

# Attack/Audit Procedure

In [6]:
# Choose number of records to target (for each, random and outlier)
num_targets = 5

# Select random target record indices
random_index = list(np.random.randint(0, 1000, num_targets))

# Select outlier target record indices
model_isoforest = IsolationForest()
preds = model_isoforest.fit_predict(data.data.iloc[:, 7:])
outlier_index = list(np.random.choice(np.where(preds == -1)[0], num_targets))

# List of all our target indices
targets = random_index + outlier_index

In [7]:
# Helper function to construct attack
def attack(dataset, target_index, generator):
    # Knowledge of the real data - assume auxiliary knowledge of the private dataset - auxiliary data from same distribution
    data_knowledge = tapas.threat_models.AuxiliaryDataKnowledge(dataset,
                        auxiliary_split=0.5, num_training_records=100, )

    # Knowledge of the generator - typically black-box access
    sdg_knowledge = tapas.threat_models.BlackBoxKnowledge(generator, num_synthetic_records=100, )

    # Define threat model with attacker goal: membership inference attack on a random record
    threat_model = tapas.threat_models.TargetedMIA(attacker_knowledge_data=data_knowledge,
                        target_record=dataset.get_records([target_index]),
                        attacker_knowledge_generator=sdg_knowledge,
                        generate_pairs=True,
                        replace_target=True,
                        iterator_tracker=tqdm.tqdm)

    # Initialize an attacker: Groundhog attack with standard parameters
    random_forest = RandomForestClassifier(n_estimators=100)
    feature_set = tapas.attacks.NaiveSetFeature() + tapas.attacks.HistSetFeature() + tapas.attacks.CorrSetFeature()
    feature_classifier = tapas.attacks.FeatureBasedSetClassifier(feature_set, random_forest)
    attacker = tapas.attacks.GroundhogAttack(feature_classifier)

    # Train the attack
    start = time.time()
    attacker.train(threat_model, num_samples=100)
    end = time.time()
    print("time it took to train the attacker: {}".format(end-start))

    # Test the attack
    start = time.time()
    summary = threat_model.test(attacker, num_samples=100)
    end = time.time()
    print("time it took to test the attacker: {}".format(end-start))

    metrics = summary.get_metrics()
    metrics["dataset"] = "Texas"

    # print("Results:\n", metrics.head())
    return summary, metrics

In [8]:
# Can try attack with several generators (not all generators work on all datasets)
generators = [Raw(), 
              CTGAN(epochs=1), 
              #DPCTGAN(epsilon=0.1, batch_size=64, epochs=1), 
              #DPCTGAN(epsilon=0.5, batch_size=64, epochs=1),
              DPCTGAN(epsilon=1, batch_size=64, epochs=1)]

Caution: auditing multiple generators and many target records can result in a very long computational runtime (this is why the generators are set to epochs=1 with small privacy budgets above, for demonstration purposes). This problem can be exacerbated by changing various parameters of the attack as well, like the num_training_records when defining the data knowledge, num_synthetic_records when defining the generator knowledge, or num_samples when training/testing the attack.

In [9]:
# To store results of attacks
all_metrics = pd.DataFrame()
all_summaries = []    # for effective epsilon calculation

# Loop through all generators
for gen in generators: 
    # Loop through all target records
    for target in targets:
        try:  
            summ, metr = attack(dataset=data, target_index=target, generator=gen)
            all_summaries.append(summ)
            all_metrics = pd.concat([all_metrics, metr], axis=0, ignore_index=True)
            # print(metr.head())
        except Exception:
            continue

100%|███████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 2532.23it/s]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


time it took to train the attacker: 1.0579280853271484


100%|███████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 3933.92it/s]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


time it took to test the attacker: 1.127197027206421


100%|███████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 3721.19it/s]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


...

Epoch 1, Loss G: 0.1128, Loss D: 0.0035
epsilon is 0.028590312727600813, alpha is 63.0
Epoch 2, Loss G: 0.1150, Loss D: 0.0065
epsilon is 0.3508497978739808, alpha is 19.0
Epoch 3, Loss G: 0.1114, Loss D: -0.0018
epsilon is 0.5118818491933068, alpha is 15.0
Epoch 4, Loss G: 0.1138, Loss D: -0.0114
epsilon is 0.6401869495928957, alpha is 13.0
Epoch 5, Loss G: 0.1166, Loss D: -0.0022
epsilon is 0.7519399509030614, alpha is 12.0
Epoch 6, Loss G: 0.1112, Loss D: 0.0041
epsilon is 0.8505949589561193, alpha is 10.6
Epoch 7, Loss G: 0.1109, Loss D: 0.0027
epsilon is 0.9421075032742222, alpha is 9.9


 99%|█████████████████████████████████████████████████████████████▍| 99/100 [05:23<00:03,  3.15s/it]/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/opacus/privacy_engine.py:638: UserWarning: The sample rate will be defined from ``batch_size`` and ``sample_size``.The returned privacy budget will be incorrect.
  warnings.warn(
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/opacus/privacy_engine.py:229: UserWarning: Secure RNG turned off. This is perfectly fine for experimentation as it allows for much faster training performance, but remember to turn it on and retrain one last time before production with ``secure_rng`` turned on.
  warnings.warn(
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/torch/nn/modules/module.py:1053: UserWarning: Using a non-full backward hook when the forward contains multiple autograd Nodes is 

Epoch 1, Loss G: 0.0063, Loss D: -0.0058
epsilon is 0.028590312727600813, alpha is 63.0
Epoch 2, Loss G: 0.0023, Loss D: -0.0064
epsilon is 0.3508497978739808, alpha is 19.0
Epoch 3, Loss G: 0.0025, Loss D: 0.0007
epsilon is 0.5118818491933068, alpha is 15.0
Epoch 4, Loss G: 0.0020, Loss D: 0.0073
epsilon is 0.6401869495928957, alpha is 13.0
Epoch 5, Loss G: 0.0034, Loss D: 0.0009
epsilon is 0.7519399509030614, alpha is 12.0
Epoch 6, Loss G: 0.0036, Loss D: 0.0107
epsilon is 0.8505949589561193, alpha is 10.6
Epoch 7, Loss G: -0.0012, Loss D: 0.0050
epsilon is 0.9421075032742222, alpha is 9.9


100%|█████████████████████████████████████████████████████████████| 100/100 [05:26<00:00,  3.27s/it]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/Users/nicklauskim/Library/Caches/pypoetry/virtualenvs/tapas-nDlO0gJj-py3.9/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/Users/nicklauskim/Documents/Research/Thesis/Code/t

time it took to test the attacker: 327.7000880241394


In [10]:
# Now, check metrics and summaries
print(all_metrics)
print(all_summaries)

   dataset target_id         generator     attack  accuracy  \
0    Texas       138               Raw  Groundhog      0.57   
1    Texas       464               Raw  Groundhog      0.58   
2    Texas       510               Raw  Groundhog      0.57   
3    Texas        94               Raw  Groundhog      0.54   
4    Texas       162               Raw  Groundhog      0.61   
5    Texas       832               Raw  Groundhog      0.75   
6    Texas       679               Raw  Groundhog      0.93   
7    Texas       762               Raw  Groundhog      0.78   
8    Texas       189               Raw  Groundhog      0.79   
9    Texas       511               Raw  Groundhog      0.84   
10   Texas       138             CTGAN  Groundhog      0.97   
11   Texas       464             CTGAN  Groundhog      0.97   
12   Texas       510             CTGAN  Groundhog      0.96   
13   Texas        94             CTGAN  Groundhog      0.97   
14   Texas       162             CTGAN  Groundhog      

# Results and Plots

In [11]:
# Get indices for only the attacks on random targets
num_attacks = all_metrics.shape[0]
random_indices = [num for i in range(0, num_attacks, num_targets*2) for num in range(i, i+num_targets)]

In [12]:
# Compare generators on random targets
report = tapas.report.BinaryLabelAttackReport(all_metrics.iloc[random_indices])
report.metrics = ["privacy_gain", "auc", "effective_epsilon"]
report.compare(comparison_column='generator', fixed_pair_columns=['attack', 'dataset'], marker_column='target_id', filepath="../figures/Texas_compare_generators")

In [16]:
# Save eff eps report for DP-CTGAN, as an example (corresponding to the last 10 summaries)
selected_summaries = all_summaries[20:]
tapas.report.EffectiveEpsilonReport(selected_summaries).publish("../figures/")

/Users/nicklauskim/Documents/Research/Thesis/Code/tapas/report/report.py:497: RuntimeWarning: divide by zero encountered in log
  low_bound = max(0, np.log(ci_tpr.low / ci_fpr.high))


Using attack Groundhog with threshold 0.34 and False.


confidence  epsilon_low  epsilon_high
0        0.90            0      0.081975
1        0.95            0      0.097378
2        0.99            0      0.133144

Computing the effective epsilon takes quite a bit of careful configuration to get appropriate results; typically it requires many attacks to be run, then many attack summaries to be fed into the EffectiveEpsilonReport() function.

In [17]:
# Compare attack for different target record types: random and outlier
all_metrics['target_type'] = (['Random']*num_targets + ['Outlier']*num_targets) * len(generators)

report = tapas.report.BinaryLabelAttackReport(all_metrics)
report.metrics = ["privacy_gain", "auc"]
report.compare(comparison_column='generator', fixed_pair_columns=['attack', 'dataset'], marker_column='target_type', filepath="../figures/Texas_random_versus_outlier")

While this notebook just serves as a quick intro to getting things up and running, there are *many* other plots and comparisons you can make using a similar process...